# ou12 Powell

In [21]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
import multiprocessing

np.random.seed(22101)

# Define the model that generates pair simulations.
yuima = importr("yuima")
n_jumpou_NIG_sim_string = """
n_jumpou_NIG = function(random_seed, num_sim,
                        mu11, mu12, mu21, mu22, 
                        sigma11, sigma12, sigma21, sigma22,
                        j11, j12, j21, j22,
                        alpha, beta1, beta2, delta0, mu1, mu2, 
                        lambda11, lambda12, lambda21, lambda22,
                        xinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-mu12*X1", "mu21-mu22*X2")
  diffusion = matrix(c("exp(sigma11)", "exp(sigma12)", "exp(sigma21)", "exp(sigma22)"), 2, 2, byrow=TRUE)
  jumpcoef = matrix(c("j11", "j12", "j21", "j22"), 2, 2, byrow=TRUE) 
  
  alpha = alpha
  beta = c(beta1, beta2)
  delta0 = delta0
  mu = c(mu1, mu2)
  Lambda = matrix(c(lambda11, lambda12, lambda21, lambda22), 2, 2, byrow=TRUE)
  
  ou_model = setModel(drift=drift, diffusion=diffusion, jump.coeff=jumpcoef, 
                      measure.type="code",
                      measure=list(df="rNIG(z, alpha, beta, delta0, mu, Lambda)"), 
                      time.variable = "t",
                      state.var=c("X1","X2"), solve.variable=c("X1","X2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    jumpou_sim = simulate(ou_model, 
                          true.par=list(
                            mu11=mu11, mu12=mu12, mu21=mu21, mu22=mu22, 
                            sigma11=sigma11, sigma12=sigma12, sigma21=sigma21, sigma22=sigma22,
                            j11=j11, j12=j12, j21=j21, j22=j22,
                            alpha=alpha, beta=beta, delta0=delta0, mu=mu, Lambda=Lambda), 
                          xinit=xinit_vec[[i]], sampling=newsamp)
    original_data = jumpou_sim@data@original.data
    one_sim_jumpou = data.frame(original_data[,1], original_data[,2])
    colnames(one_sim_jumpou) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_jumpou
  }
  return(n_sim_data)
}

n_pair_prices = read.csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Generator/sp500_20180101_20181231_pair_prices.csv", row.names=1)
n_log_pair_prices = log(n_pair_prices)
xinit_vec = list()
for (i in 1:(dim(n_pair_prices)[2]/2)){
  xinit_vec[i] = as.numeric(n_log_pair_prices[1, (2*i-1):(2*i)])
}
"""

n_jumpou_NIG_sim = SignatureTranslatedAnonymousPackage(n_jumpou_NIG_sim_string, "n_jumpou_NIG_sim")
def n_jumpou_simulation(random_seed, num_sim,
                        mu11, mu12, mu21, mu22, 
                        sigma11, sigma12, sigma21, sigma22,
                        j11, j12, j21, j22,
                        alpha, beta1, beta2, delta0, mu1, mu2, 
                        lambda11, lambda12, lambda21, lambda22,
                        xinit_vec, T0, T, length):
    """num_sim simulations of bivariate Ornstein-Uhlenbeck process,
    length = length of one series
    """
    n_sim_data = pd.DataFrame(
        n_jumpou_NIG_sim.n_jumpou_NIG(random_seed, num_sim,
                                      mu11, mu12, mu21, mu22, 
                                      sigma11, sigma12, sigma21, sigma22,
                                      j11, j12, j21, j22,
                                      alpha, beta1, beta2, delta0, mu1, mu2, 
                                      lambda11, lambda12, lambda21, lambda22,
                                      xinit_vec, T0, T, length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return

    
def cal_stats(n_return, n_price=None):
    # (different expressions of calculation from intro to stat finance)
    # 4 statistics
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    
    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, skew1, skew2, kurtosis1, kurtosis2, autocorr1, autocorr2])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2']
    return stats_data



def loss_function(params):
    """n_real_stats is a global amount calculated outside the function"""
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    n_sim_log_price = n_jumpou_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu12=params[1], mu21=params[2], mu22=params[3], 
        sigma11=params[4], sigma12=params[5], sigma21=params[6], sigma22=params[7],
        j11=params[8], j12=params[9], j21=params[10], j22=params[11],
        alpha=alpha, beta1=beta1, beta2=beta2, delta0=delta0, mu1=mu1, mu2=mu2, 
        lambda11=lambda11, lambda12=lambda12, lambda21=lambda21, lambda22=lambda22,
        xinit_vec=xinit_vec, T0=T0, T=T, length=length)
    
    print(n_sim_log_price.iloc[5, 5])
    n_sim_price = log_price_to_price(n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_sim_return)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("sp500_20180101_20181231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("sp500_20180101_20181231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=None)


xinit_vec = []
for i in range(int(real_log_price.shape[1]/2)):
    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




alpha = 2
beta1 = 0
beta2 = 0
delta0 = 0.55
mu1 = 0
mu2 = 0
lambda11 = 1
lambda12 = 0
lambda21 = 0
lambda22 = 1






initial0 = [1, 1, 1, 1,
            1, 1, 1, 1,
            1, 1, 1, 1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(0., None), (0., None), (0., None), (0., None),
                       (None, None), (None, None), (None, None), (None, None),
                       (None, None), (None, None), (None, None), (None, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)


 [1] 1 1 1 1 1 1 1 1 1 1 1 1

5.397056061058307
return_mean1                271.466379
return_mean2                263.419445
return_sd1                 5718.224490
return_sd2                 5704.275172
return_skew1                164.503993
return_skew2                164.503993
return_kurtosis1           1101.686307
return_kurtosis2           1683.204673
return_autocorrelation1      17.255656
return_autocorrelation2      17.002631
dtype: float64
15105.54273845948
----------
 [1] 1.115092 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

4.883134650812212
return_mean1                248.995054
return_mean2                245.945151
return_sd1                 5702.234039
return_sd2                 5688.400423
return_skew1                167.700623
return_skew2                167.700623
return_kurtosis1           1099.604525
return_kurtosis2           1658.565766
return_autocorrelation1      17.452959
return_autocorrelation2      1

5.419042630872681
return_mean1                257.252768
return_mean2                252.191514
return_sd1                 5715.947655
return_sd2                 5702.110038
return_skew1                163.348087
return_skew2                163.348087
return_kurtosis1           1093.371797
return_kurtosis2           1686.453885
return_autocorrelation1      17.535781
return_autocorrelation2      17.336149
dtype: float64
15068.895761427224
----------
 [1] 1.115399 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

4.565080634407215
return_mean1                247.206986
return_mean2                246.931414
return_sd1                 5748.887971
return_sd2                 5734.901777
return_skew1                179.541235
return_skew2                179.541235
return_kurtosis1           1154.070243
return_kurtosis2           1751.980986
return_autocorrelation1      17.281357
return_autocorrelation2      17.434408
dtype: float64
15277

4.288440397247797
return_mean1                246.708496
return_mean2                245.363465
return_sd1                 5711.276988
return_sd2                 5697.386462
return_skew1                175.796554
return_skew2                175.796554
return_kurtosis1           1181.109283
return_kurtosis2           1770.858863
return_autocorrelation1      18.875352
return_autocorrelation2      18.254565
dtype: float64
15241.426582716527
----------
 [1] 1.114923 1.115092 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

3.794838769103599
return_mean1                268.202709
return_mean2                255.609678
return_sd1                 5730.518232
return_sd2                 5715.503113
return_skew1                168.852509
return_skew2                168.852509
return_kurtosis1           1116.657698
return_kurtosis2           1683.500354
return_autocorrelation1      18.672986
return_autocorrelation2      19.867245
dtype: float64
15146

4.308625624274912
return_mean1                258.896259
return_mean2                246.975545
return_sd1                 5730.641913
return_sd2                 5716.106280
return_skew1                166.988899
return_skew2                166.988899
return_kurtosis1           1143.126853
return_kurtosis2           1724.125095
return_autocorrelation1      16.130618
return_autocorrelation2      15.506246
dtype: float64
15185.486608192876
----------
 [1] 1.114923 1.064557 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

4.634608780711356
return_mean1                258.302802
return_mean2                253.613430
return_sd1                 5687.454755
return_sd2                 5672.931455
return_skew1                169.630640
return_skew2                169.630640
return_kurtosis1           1108.164785
return_kurtosis2           1707.977127
return_autocorrelation1      17.704571
return_autocorrelation2      17.903158
dtype: float64
15063

4.733306937197033
return_mean1                265.410653
return_mean2                267.850216
return_sd1                 5746.216043
return_sd2                 5731.593963
return_skew1                166.130080
return_skew2                166.130080
return_kurtosis1           1108.955191
return_kurtosis2           1678.274989
return_autocorrelation1      17.880913
return_autocorrelation2      18.331449
dtype: float64
15166.77357584071
----------
 [1] 1.114923 1.064557 1.278271 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

5.801819079256987
return_mean1                270.784861
return_mean2                257.710165
return_sd1                 5693.404146
return_sd2                 5678.928377
return_skew1                164.037321
return_skew2                164.037321
return_kurtosis1           1101.037657
return_kurtosis2           1691.774117
return_autocorrelation1      16.677028
return_autocorrelation2      18.260855
dtype: float64
15056.

...

5.028694250875526
return_mean1                 47.074122
return_mean2                 43.004317
return_sd1                   87.234207
return_sd2                   98.909408
return_skew1                168.188474
return_skew2                168.188474
return_kurtosis1           1113.443378
return_kurtosis2           1689.832846
return_autocorrelation1      17.869284
return_autocorrelation2      16.009655
dtype: float64
3449.7541646413124
----------
 [1]  4.01892463  0.97496238  3.52382986  0.83743539 -3.61794976 -1.41306750
 [7] -1.40361978 -4.72195169 -0.02840171 -0.08423746  0.09397719  0.01336152

4.976112592208517
return_mean1                 44.648822
return_mean2                 43.600618
return_sd1                   86.989662
return_sd2                   98.498910
return_skew1                164.636528
return_skew2                164.636528
return_kurtosis1           1127.680056
return_kurtosis2           1700.377107
return_autocorrelation1      16.889290
return_autocorrelation2

5.049649320796849
return_mean1                 45.720321
return_mean2                 41.761343
return_sd1                   86.738611
return_sd2                   98.588398
return_skew1                166.368671
return_skew2                166.368671
return_kurtosis1           1130.369298
return_kurtosis2           1713.299145
return_autocorrelation1      17.704129
return_autocorrelation2      18.519833
dtype: float64
3485.438421927913
----------
 [1]  4.01892463  0.97496238  3.52382986  0.83743539 -3.61794976 -1.41306750
 [7] -1.40361978 -4.72195169 -0.02840171 -0.08404128  0.06174811  0.01336152

5.01819767311477
return_mean1                 45.051513
return_mean2                 42.474877
return_sd1                   87.862003
return_sd2                   96.747984
return_skew1                165.258447
return_skew2                165.258447
return_kurtosis1           1101.062943
return_kurtosis2           1688.827856
return_autocorrelation1      17.069807
return_autocorrelation2  

5.035062116757705
return_mean1                 45.787190
return_mean2                 43.144638
return_sd1                   88.457093
return_sd2                   96.752490
return_skew1                164.329899
return_skew2                164.329899
return_kurtosis1           1124.808147
return_kurtosis2           1698.539572
return_autocorrelation1      15.966890
return_autocorrelation2      18.568480
dtype: float64
3460.684299845816
----------
 [1]  4.01892463  0.97496238  3.52382986  0.83743539 -3.61794976 -1.41306750
 [7] -1.40361978 -4.72195169 -0.02840171 -0.08404128  0.06177664  0.01336152

4.947936983890857
return_mean1                 45.936805
return_mean2                 43.569343
return_sd1                   88.510707
return_sd2                   96.266493
return_skew1                166.646911
return_skew2                166.646911
return_kurtosis1           1160.464039
return_kurtosis2           1693.838055
return_autocorrelation1      17.384535
return_autocorrelation2 

5.028838012956824
return_mean1                 46.106504
return_mean2                 43.133848
return_sd1                   87.106128
return_sd2                   97.895173
return_skew1                167.823653
return_skew2                167.823653
return_kurtosis1           1083.159343
return_kurtosis2           1682.612194
return_autocorrelation1      18.547648
return_autocorrelation2      17.551429
dtype: float64
3411.7595736922767
----------
 [1]  4.01892463  0.97496238  3.52382986  0.83743539 -3.61794976 -1.41306750
 [7] -1.40361978 -4.72195169 -0.02840171 -0.08404128  0.06179427 -0.05922855

4.968678330172925
return_mean1                 45.550324
return_mean2                 41.546938
return_sd1                   87.456589
return_sd2                   94.116885
return_skew1                170.504385
return_skew2                170.504385
return_kurtosis1           1164.150199
return_kurtosis2           1669.319615
return_autocorrelation1      17.444533
return_autocorrelation2

4.946845740830437
return_mean1                 45.790420
return_mean2                 40.665579
return_sd1                   86.984971
return_sd2                   96.175943
return_skew1                166.224700
return_skew2                166.224700
return_kurtosis1           1116.174425
return_kurtosis2           1671.152250
return_autocorrelation1      18.239254
return_autocorrelation2      18.434611
dtype: float64
3426.066851710018
----------
 [1]  4.01892463  0.97496238  3.52382986  0.83743539 -3.61794976 -1.41306750
 [7] -1.40361978 -4.72195169 -0.02840171 -0.08404128  0.06179427 -0.06554249

4.96542272535661
return_mean1                 45.350884
return_mean2                 41.301337
return_sd1                   87.556277
return_sd2                   97.551994
return_skew1                164.653317
return_skew2                164.653317
return_kurtosis1           1096.687551
return_kurtosis2           1694.445465
return_autocorrelation1      18.436053
return_autocorrelation2  

In [3]:
real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=None)


xinit_vec = []
for i in range(int(real_log_price.shape[1]/2)):
    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]




n_sim_jumpou_log_prices = n_jumpou_simulation(
    random_seed=9868, num_sim=248,
    
    mu11=4.01892463, mu12=0.97496238, 
    mu21=3.52382986, mu22=0.83743539,
    
    sigma11=-3.61794976, sigma12=-1.4130675, 
    sigma21=-1.40361978, sigma22=-4.72195169,
    
    j11=-0.02840171, j12=-0.08404128, 
    j21=0.06179427, j22=-0.06551355,
    
    alpha=2, 
    beta1=0, beta2=0, 
    delta0=0.55, 
    mu1=0, mu2=0,
    lambda11=1, lambda12=0, 
    lambda21=0, lambda22=1,
    
    xinit_vec=xinit_vec, T0=0, T=1, length=250)

n_sim_jumpou_pair_prices = log_price_to_price(n_log_price=n_sim_jumpou_log_prices)
n_sim_jumpou_pair_returns = price_to_return(n_price=n_sim_jumpou_pair_prices)

print(n_sim_jumpou_log_prices)
print(n_sim_jumpou_pair_prices)
print(n_sim_jumpou_pair_returns)

n_sim_jumpou_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ou_jump12/n_sim_jumpou_pair_prices.csv")
n_sim_jumpou_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ou_jump12/n_sim_jumpou_pair_returns.csv")


          0         1         2         3         4         5         6    \
0    3.647595  4.134696  4.584573  4.021957  7.338973  5.094021  6.960993   
1    3.652329  4.152126  4.585297  4.051485  7.315835  5.093097  6.944799   
2    3.670008  4.162101  4.605659  4.041599  7.291654  5.090622  6.929786   
3    3.652222  4.150641  4.605712  4.040459  7.277264  5.105885  6.920566   
4    3.626437  4.141639  4.599941  4.036050  7.239077  5.090104  6.906213   
..        ...       ...       ...       ...       ...       ...       ...   
246  4.105496  4.576030  3.951896  4.047034  5.355811  4.600818  5.519443   
247  4.119426  4.581680  3.976580  4.063373  5.340490  4.619261  5.500912   
248  4.144466  4.609462  3.968689  4.064069  5.341793  4.621570  5.499179   
249  4.151585  4.589554  3.972067  4.101748  5.323718  4.615004  5.479218   
250  4.143562  4.593582  3.958349  4.110139  5.321415  4.620308  5.471581   

          7         8         9    ...       486       487       488  \
0  

# jump12 with more cal_stats

In [7]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

np.random.seed(22101)

# Define the model that generates pair simulations.
yuima = importr("yuima")
n_jumpou_NIG_sim_string = """
n_jumpou_NIG = function(random_seed, num_sim,
                        mu11, mu12, mu21, mu22, 
                        sigma11, sigma12, sigma21, sigma22,
                        j11, j12, j21, j22,
                        alpha, beta1, beta2, delta0, mu1, mu2, 
                        lambda11, lambda12, lambda21, lambda22,
                        xinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-mu12*X1", "mu21-mu22*X2")
  diffusion = matrix(c("exp(sigma11)", "exp(sigma12)", "exp(sigma21)", "exp(sigma22)"), 2, 2, byrow=TRUE)
  jumpcoef = matrix(c("j11", "j12", "j21", "j22"), 2, 2, byrow=TRUE) 
  
  alpha = alpha
  beta = c(beta1, beta2)
  delta0 = delta0
  mu = c(mu1, mu2)
  Lambda = matrix(c(lambda11, lambda12, lambda21, lambda22), 2, 2, byrow=TRUE)
  
  ou_model = setModel(drift=drift, diffusion=diffusion, jump.coeff=jumpcoef, 
                      measure.type="code",
                      measure=list(df="rNIG(z, alpha, beta, delta0, mu, Lambda)"), 
                      time.variable = "t",
                      state.var=c("X1","X2"), solve.variable=c("X1","X2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    jumpou_sim = simulate(ou_model, 
                          true.par=list(
                            mu11=mu11, mu12=mu12, mu21=mu21, mu22=mu22, 
                            sigma11=sigma11, sigma12=sigma12, sigma21=sigma21, sigma22=sigma22,
                            j11=j11, j12=j12, j21=j21, j22=j22,
                            alpha=alpha, beta=beta, delta0=delta0, mu=mu, Lambda=Lambda), 
                          xinit=xinit_vec[[i]], sampling=newsamp)
    original_data = jumpou_sim@data@original.data
    one_sim_jumpou = data.frame(original_data[,1], original_data[,2])
    colnames(one_sim_jumpou) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_jumpou
  }
  return(n_sim_data)
}

n_pair_prices = read.csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Generator/sp500_20180101_20181231_pair_prices.csv", row.names=1)
n_log_pair_prices = log(n_pair_prices)
xinit_vec = list()
for (i in 1:(dim(n_pair_prices)[2]/2)){
  xinit_vec[i] = as.numeric(n_log_pair_prices[1, (2*i-1):(2*i)])
}
"""

n_jumpou_NIG_sim = SignatureTranslatedAnonymousPackage(n_jumpou_NIG_sim_string, "n_jumpou_NIG_sim")
def n_jumpou_simulation(random_seed, num_sim,
                        mu11, mu12, mu21, mu22, 
                        sigma11, sigma12, sigma21, sigma22,
                        j11, j12, j21, j22,
                        alpha, beta1, beta2, delta0, mu1, mu2, 
                        lambda11, lambda12, lambda21, lambda22,
                        xinit_vec, T0, T, length):
    """num_sim simulations of bivariate Ornstein-Uhlenbeck process,
    length = length of one series
    """
    n_sim_data = pd.DataFrame(
        n_jumpou_NIG_sim.n_jumpou_NIG(random_seed, num_sim,
                                      mu11, mu12, mu21, mu22, 
                                      sigma11, sigma12, sigma21, sigma22,
                                      j11, j12, j21, j22,
                                      alpha, beta1, beta2, delta0, mu1, mu2, 
                                      lambda11, lambda12, lambda21, lambda22,
                                      xinit_vec, T0, T, length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return


def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef

def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)
    
    
    # adf test on original prices: test if the price difference of the two time series is stationary
    p_values = []
    for i in range(int(real_price.shape[1]/2)):
        reg = LinearRegression().fit(np.array(price_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, 
                               autocorr1, autocorr2, corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
                               p_values])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'price_adf_p_values']
    return stats_data




def loss_function(params):
    """n_real_stats is a global amount calculated outside the function"""
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    n_sim_log_price = n_jumpou_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu12=params[1], mu21=params[2], mu22=params[3], 
        sigma11=params[4], sigma12=params[5], sigma21=params[6], sigma22=params[7],
        j11=params[8], j12=params[9], j21=params[10], j22=params[11],
        alpha=alpha, beta1=beta1, beta2=beta2, delta0=delta0, mu1=mu1, mu2=mu2, 
        lambda11=lambda11, lambda12=lambda12, lambda21=lambda21, lambda22=lambda22,
        xinit_vec=xinit_vec, T0=T0, T=T, length=length)
    
    n_sim_price = log_price_to_price(n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_sim_return, n_sim_price)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("sp500_20180101_20181231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("sp500_20180101_20181231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
for i in range(int(real_log_price.shape[1]/2)):
    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




alpha = 2
beta1 = 0
beta2 = 0
delta0 = 0.55
mu1 = 0
mu2 = 0
lambda11 = 1
lambda12 = 0
lambda21 = 0
lambda22 = 1






initial0 = [1, 1, 1, 1,
            1, 1, 1, 1,
            1, 1, 1, 1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(0., None), (0., None), (0., None), (0., None),
                       (None, None), (None, None), (None, None), (None, None),
                       (None, None), (None, None), (None, None), (None, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)


 [1] 1 1 1 1 1 1 1 1 1 1 1 1

5.397056061058307
return_mean1                     271.466379
return_mean2                     263.419445
return_sd1                      5718.224490
return_sd2                      5704.275172
return_skew1                     164.503993
return_skew2                     164.503993
return_kurtosis1                1101.686307
return_kurtosis2                1683.204673
return_autocorrelation1           17.255656
return_autocorrelation2           17.002631
return_correlation_ts1_lag_0     157.650853
return_correlation_ts1_lag_1      16.385533
return_correlation_ts1_lag_2      18.324252
return_correlation_ts1_lag_3      18.541792
return_correlation_ts2_lag_1      19.830837
return_correlation_ts2_lag_2      18.707386
return_correlation_ts2_lag_3      18.474486
price_adf_p_values                60.458853
dtype: float64
15433.916730089877
----------
 [1] 1.115092 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.0000

3.8081065061962605
return_mean1                     250.810212
return_mean2                     253.203247
return_sd1                      5720.245928
return_sd2                      5706.311653
return_skew1                     170.828859
return_skew2                     170.828859
return_kurtosis1                1143.567057
return_kurtosis2                1710.059349
return_autocorrelation1           17.197322
return_autocorrelation2           17.445244
return_correlation_ts1_lag_0     157.650849
return_correlation_ts1_lag_1      17.643989
return_correlation_ts1_lag_2      17.737404
return_correlation_ts1_lag_3      18.905309
return_correlation_ts2_lag_1      17.892265
return_correlation_ts2_lag_2      18.783315
return_correlation_ts2_lag_3      18.240647
price_adf_p_values                66.509547
dtype: float64
15493.861053967968
----------
 [1] 1.120207 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

4.566668236928714
return_

5.840606952649323
return_mean1                     253.963651
return_mean2                     253.450719
return_sd1                      5718.796088
return_sd2                      5704.851379
return_skew1                     164.085121
return_skew2                     164.085121
return_kurtosis1                1166.411418
return_kurtosis2                1753.676071
return_autocorrelation1           18.173166
return_autocorrelation2           17.295480
return_correlation_ts1_lag_0     157.650858
return_correlation_ts1_lag_1      16.841281
return_correlation_ts1_lag_2      17.589873
return_correlation_ts1_lag_3      20.669246
return_correlation_ts2_lag_1      18.120946
return_correlation_ts2_lag_2      18.000820
return_correlation_ts2_lag_3      19.156341
price_adf_p_values                59.623056
dtype: float64
15542.440635563924
----------
 [1] 1.114989 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

4.475306255724474
return_m

4.839093000210999
return_mean1                     261.797469
return_mean2                     258.915158
return_sd1                      5714.270499
return_sd2                      5700.406752
return_skew1                     168.599437
return_skew2                     168.599437
return_kurtosis1                1102.194387
return_kurtosis2                1678.630408
return_autocorrelation1           17.505239
return_autocorrelation2           17.722592
return_correlation_ts1_lag_0     157.650841
return_correlation_ts1_lag_1      16.921848
return_correlation_ts1_lag_2      17.470487
return_correlation_ts1_lag_3      21.179133
return_correlation_ts2_lag_1      18.337700
return_correlation_ts2_lag_2      18.208714
return_correlation_ts2_lag_3      18.255839
price_adf_p_values                60.494514
dtype: float64
15417.160454230732
----------
 [1] 1.114925 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

5.761754541647635
return_m

4.146344054704772
return_mean1                     262.460236
return_mean2                     268.771406
return_sd1                      5687.081245
return_sd2                      5672.668468
return_skew1                     173.967408
return_skew2                     173.967408
return_kurtosis1                1176.770618
return_kurtosis2                1794.501329
return_autocorrelation1           18.235619
return_autocorrelation2           17.430182
return_correlation_ts1_lag_0     157.650597
return_correlation_ts1_lag_1      16.025800
return_correlation_ts1_lag_2      18.155686
return_correlation_ts1_lag_3      18.579447
return_correlation_ts2_lag_1      19.570301
return_correlation_ts2_lag_2      18.654128
return_correlation_ts2_lag_3      18.308975
price_adf_p_values                63.185035
dtype: float64
15575.983888431474
----------
 [1] 1.114924 1.087271 1.000000 1.000000 1.000000 1.000000 1.000000 1.000000
 [9] 1.000000 1.000000 1.000000 1.000000

4.3893930199451
return_mea

...

5.014437797239761
return_mean1                      46.736474
return_mean2                      77.258262
return_sd1                       105.391805
return_sd2                        94.798156
return_skew1                     170.996252
return_skew2                     170.996252
return_kurtosis1                1124.989182
return_kurtosis2                1703.705580
return_autocorrelation1           17.817730
return_autocorrelation2           18.112054
return_correlation_ts1_lag_0      34.434553
return_correlation_ts1_lag_1      16.196573
return_correlation_ts1_lag_2      16.749288
return_correlation_ts1_lag_3      20.612470
return_correlation_ts2_lag_1      17.891444
return_correlation_ts2_lag_2      16.384854
return_correlation_ts2_lag_3      18.604964
price_adf_p_values                76.298748
dtype: float64
3747.97464213736
----------
 [1]  3.89997295  0.99716927  7.73216673  1.56916890 -1.21051715 -3.44598083
 [7] -2.79223165 -1.41713142  0.02339559 -0.12915799 -0.04765816  0.07

5.00041907284618
return_mean1                      52.303996
return_mean2                      77.404701
return_sd1                       107.369352
return_sd2                        97.800965
return_skew1                     165.968616
return_skew2                     165.968616
return_kurtosis1                1113.146859
return_kurtosis2                1736.855285
return_autocorrelation1           18.111771
return_autocorrelation2           18.053956
return_correlation_ts1_lag_0      41.807883
return_correlation_ts1_lag_1      17.688640
return_correlation_ts1_lag_2      17.992259
return_correlation_ts1_lag_3      18.834836
return_correlation_ts2_lag_1      19.303469
return_correlation_ts2_lag_2      18.172750
return_correlation_ts2_lag_3      19.767513
price_adf_p_values                76.509734
dtype: float64
3783.0612024503075
----------
 [1]  3.89997295  0.99716927  7.73216673  1.56916890 -1.21051715 -3.44598083
 [7] -2.79223165 -1.41713142  0.02339559 -0.12915799 -0.04765816  0.1

5.030423231201694
return_mean1                      50.630281
return_mean2                      76.989183
return_sd1                       108.764758
return_sd2                        95.122332
return_skew1                     175.226305
return_skew2                     175.226305
return_kurtosis1                1137.118830
return_kurtosis2                1674.382372
return_autocorrelation1           17.362035
return_autocorrelation2           19.563475
return_correlation_ts1_lag_0      41.212689
return_correlation_ts1_lag_1      16.903062
return_correlation_ts1_lag_2      18.244055
return_correlation_ts1_lag_3      18.580121
return_correlation_ts2_lag_1      18.719528
return_correlation_ts2_lag_2      19.303449
return_correlation_ts2_lag_3      18.728140
price_adf_p_values                85.403155
dtype: float64
3767.4800747569852
----------
 [1]  3.89997295  0.99716927  7.73216673  1.56916890 -1.21051715 -3.44598083
 [7] -2.79223165 -1.41713142  0.02339559 -0.12915799 -0.04765816  0.

5.030677636838177
return_mean1                      47.944884
return_mean2                      76.573312
return_sd1                       104.064937
return_sd2                        95.609898
return_skew1                     179.595207
return_skew2                     179.595207
return_kurtosis1                1112.248311
return_kurtosis2                1729.509376
return_autocorrelation1           18.250618
return_autocorrelation2           17.880791
return_correlation_ts1_lag_0      41.987135
return_correlation_ts1_lag_1      17.275684
return_correlation_ts1_lag_2      18.118284
return_correlation_ts1_lag_3      18.780399
return_correlation_ts2_lag_1      18.809878
return_correlation_ts2_lag_2      17.765738
return_correlation_ts2_lag_3      18.479794
price_adf_p_values                84.287426
dtype: float64
3796.7768797734666
----------
 [1]  3.89997295  0.99716927  7.73216673  1.56916890 -1.21051715 -3.44598083
 [7] -2.79223165 -1.41713142  0.02339559 -0.12915799 -0.04765816  0.

5.069372729251693
return_mean1                      48.610908
return_mean2                      76.382710
return_sd1                       107.794470
return_sd2                        97.895158
return_skew1                     178.455326
return_skew2                     178.455326
return_kurtosis1                1180.929206
return_kurtosis2                1741.758343
return_autocorrelation1           17.118489
return_autocorrelation2           17.436822
return_correlation_ts1_lag_0      39.757751
return_correlation_ts1_lag_1      17.111376
return_correlation_ts1_lag_2      16.190237
return_correlation_ts1_lag_3      21.102642
return_correlation_ts2_lag_1      18.023414
return_correlation_ts2_lag_2      18.090759
return_correlation_ts2_lag_3      18.294647
price_adf_p_values                91.771860
dtype: float64
3885.1794436583436
----------
3885.1794436583436


In [ ]:
real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=None)


xinit_vec = []
for i in range(int(real_log_price.shape[1]/2)):
    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]



params = FloatVector(res.x)
n_sim_jumpou_log_prices = n_jumpou_simulation(
    random_seed=9868, num_sim=248,
    
    mu11=3.89997295, mu12=0.99716927, 
    mu21=7.73216673, mu22=1.56916890,
    
    sigma11=-1.21051715, sigma12=-3.44598083, 
    sigma21=-2.79223165, sigma22=-1.41713142,
    
    j11=0.02339559, j12=-0.12915799, 
    j21=-0.04765816, j22=0.11450663,
    
    alpha=2, 
    beta1=0, beta2=0, 
    delta0=0.55, 
    mu1=0, mu2=0,
    lambda11=1, lambda12=0, 
    lambda21=0, lambda22=1,
    
    xinit_vec=xinit_vec, T0=0, T=1, length=250)

n_sim_jumpou_pair_prices = log_price_to_price(n_log_price=n_sim_jumpou_log_prices)
n_sim_jumpou_pair_returns = price_to_return(n_price=n_sim_jumpou_pair_prices)

print(n_sim_jumpou_log_prices)
print(n_sim_jumpou_pair_prices)
print(n_sim_jumpou_pair_returns)

n_sim_jumpou_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ou_jump12/n_sim_jumpou_pair_prices.csv")
n_sim_jumpou_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/ou_jump12/n_sim_jumpou_pair_returns.csv")
